In [1]:
import panel as pn
import pandas as pd
import scipy.stats as stats
from sqlalchemy import create_engine
import hvplot.pandas
from datetime import datetime, timedelta
from script import processing
import numpy as np
pn.extension()
db_url = 'sqlite:///instance/local.db'
engine = create_engine(db_url)
import plotly.express as px
pn.extension('mathjax')

In [2]:
%load_ext autoreload
%autoreload 2

In [3]:
p_eval_df = None
calculated_b_stock = None
calculated_p_stock = None
# load benchmark stock
with engine.connect() as connection:
    calculated_b_stock = pd.read_sql('calculated_b_stock', con=connection)
    calculated_p_stock = pd.read_sql('calculated_p_stock', con=connection)
    p_eval_df = pd.read_sql('p_eval_result', con=connection)

In [139]:
## check why activate return and nominal return is not same 
# start_date = p_eval_df['date'].min()
# start_date = datetime(2022, 12, 14)
start_date = datetime(2023,6,25)
end_date = p_eval_df['date'].max()
print(end_date)
ticker = "601117.XSHG"
attributes_df = processing.calculate_attributes_between_dates(
    start_date, end_date, calculated_b_stock=calculated_b_stock, calculated_p_stock=calculated_p_stock)
total_attributes = attributes_df.aggregate({
        'interaction': 'sum',
        'allocation': 'sum',
        'selection': 'sum',
        'active_return': 'sum',
        'notional_return': 'sum'
    }) 
# print(attributes_df.columns)
print(total_attributes)
return_df = processing.calculate_return(p_eval_df, start_date, end_date)
return_df
most_recent_row = return_df.tail(1)
# print(return_df.head(1))
most_recent_row




2023-06-29 00:00:00
interaction        0.012116
allocation         0.002211
selection         -0.012116
active_return      0.002211
notional_return    0.002211
dtype: float64


date  portfolio_return_p  portfolio_pct_p  portfolio_return_b  \
600 2023-06-29            0.343213         0.006552           -0.017097   

     portfolio_pct_b      mkt_cap  prev_mkt_cap       pnl      risk  \
600        -0.000125  1219.334595   1211.396987  7.937608  0.309501   

     active_return  tracking_error     cum_pnl  return_p  return_b  
600       0.002785        0.218361  140.338486  0.014219  0.011434

In [124]:
1038.573137 * (1 + 0.174048)

1219.334714348576

In [137]:
# portfolio return
attributes_df['w_return_p'] = attributes_df.pct_p * attributes_df.prev_w_in_p_p
attributes_df.w_return_p.sum()

0.01448137201285984

In [129]:
0.17190200433908703 - 0.07639191349286556

0.09551009084622147

In [138]:
# benchmark return
attributes_df['w_return_b'] = attributes_df.pct_b * attributes_df.prev_w_in_p_b
attributes_df.w_return_b.sum()

0.011250737770502067

In [120]:
selected_df = p_eval_df[p_eval_df.date.between(start_date, end_date)]
selected_df.iloc[0, selected_df.columns.get_indexer(
    ['portfolio_pct_p', 'portfolio_pct_b'])] = 0
selected_df['return_p'] = (1 + selected_df.portfolio_pct_p).cumprod()
selected_df

/var/folders/v5/2108rh5964q9j741wg_s8r1w0000gn/T/ipykernel_87460/2230555833.py:4: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  selected_df['return_p'] = (1 + selected_df.portfolio_pct_p).cumprod()


date  portfolio_return_p  portfolio_pct_p  portfolio_return_b  \
471 2022-12-14            0.151775         0.000000            0.002796   
472 2022-12-15            0.166816         0.013638            0.004505   
473 2022-12-16            0.156618        -0.009792           -0.000671   
474 2022-12-19            0.144766        -0.012217           -0.022720   
475 2022-12-20            0.140936        -0.003925           -0.032668   
..         ...                 ...              ...                 ...   
596 2023-06-21            0.338226        -0.012860           -0.012265   
597 2023-06-26            0.327466        -0.009151           -0.028546   
598 2023-06-27            0.339179         0.010630           -0.016308   
599 2023-06-28            0.335389        -0.002982           -0.016974   
600 2023-06-29            0.343213         0.006552           -0.017097   

     portfolio_pct_b      mkt_cap  prev_mkt_cap        pnl      risk  \
471         0.000000  1038.573137   1043.453255  -4.880117  0.327324   
472         0.001707  1052.737107   1038.573137  14.163970  0.327122   
473        -0.005172  1042.429190   1052.737107 -10.307917  0.326859   
474        -0.022046  1029.693832   1042.429190 -12.735359  0.326642   
475        -0.009947  1025.652205   1029.693832  -4.041626  0.326312   
..               ...          ...           ...        ...       ...   
596        -0.020746  1213.343064   1229.149762 -15.806698  0.310372   
597        -0.016269  1202.239760   1213.343064 -11.103304  0.310175   
598         0.012234  1215.019735   1202.239760  12.779975  0.309985   
599        -0.000665  1211.396987   1215.019735  -3.622748  0.309735   
600        -0.000125  1219.334595   1211.396987   7.937608  0.309501   

     active_return  tracking_error     cum_pnl  return_p  
471      -0.000508        0.225463  -40.422972  1.000000  
472       0.011931        0.225384  -26.259002  1.013638  
473      -0.004619        0.225175  -36.566919  1.003713  
474       0.009829        0.225043  -49.302277  0.991450  
475       0.006022        0.224844  -53.343904  0.987559  
..             ...             ...         ...       ...  
596       0.007886        0.219003  134.346955  1.168279  
597       0.007118        0.218860  123.243651  1.157588  
598      -0.001604        0.218682  136.023626  1.169893  
599      -0.002316        0.218507  132.400878  1.166405  
600       0.006678        0.218361  140.338486  1.174048  

[130 rows x 13 columns]

In [140]:
p_eval_df.columns

Index(['date', 'portfolio_return_p', 'portfolio_pct_p', 'portfolio_return_b',
       'portfolio_pct_b', 'mkt_cap', 'prev_mkt_cap', 'pnl', 'risk',
       'active_return', 'tracking_error', 'cum_pnl'],
      dtype='object')